## 1. Installation des dépendances

`!pip install requests beautifulsoup4 scrapy pandas lxml`




In [ ]:
!pip install requests beautifulsoup4 scrapy pandas lxml

### 1.1. Importation des bibliothèques

In [ ]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import time
import random

### 1.2. Test du site - Réponse serveur

In [ ]:
url = "https://www.hellowork.com/fr-fr/emploi/recherche.html"


headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36'
}

response = requests.get(url, headers=headers)

print("Code HTTP :", response.status_code)
print("Contenu :", response.text[:500])

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.hellowork.com:443
DEBUG:urllib3.connectionpool:https://www.hellowork.com:443 "GET /fr-fr/emploi/recherche.html HTTP/1.1" 200 101868


Code HTTP : 200
Contenu : <!DOCTYPE html>
<html lang="fr-fr"
    class="tw-scroll-smooth"
    data-controller="fetch-account-data"
    data-fetch-account-data-url-value="/fr-fr/compte/accountdata"
>
<head>
    
<!--
En visualisant le code source vous acceptez les CGU accessibles à l’adresse : https://www.hellowork.comhttps://www.hellowork-group.com/fr/legal/cgu-hellowork/
Notamment l’article 8.2
L’Utilisateur peut uniquement utiliser le Site aux fins d’accéder aux Services, ce exclusivement à des fins privées et non comm


## Scrapping via Scrappy

In [ ]:
!pip install nest_asyncio

import nest_asyncio
nest_asyncio.apply()


In [ ]:
#!/usr/bin/env python3
import sys
import asyncio

# Vérifier et nettoyer un réacteur existant
if 'twisted.internet.reactor' in sys.modules:
    # Sauvegarder si vous avez besoin d'accéder au réacteur plus tard
    saved_modules = {}
    for key in list(sys.modules.keys()):
        if 'twisted' in key and 'reactor' in key:
            saved_modules[key] = sys.modules[key]
            del sys.modules[key]

    # Essayer aussi de nettoyer twisted.internet
    if 'twisted.internet' in sys.modules:
        del sys.modules['twisted.internet']

# Configurer asyncio
if sys.platform == 'win32':
    asyncio.set_event_loop_policy(asyncio.WindowsSelectorEventLoopPolicy())

# Créer une nouvelle boucle d'événements
asyncio.set_event_loop(asyncio.new_event_loop())

# Importer et installer asyncioreactor
from twisted.internet import asyncioreactor
try:
    asyncioreactor.install(asyncio.get_event_loop())
except Exception as e:
    print(f"Erreur lors de l'installation du réacteur: {e}")
    # Continuer malgré l'erreur, le réacteur est peut-être déjà installé

# Maintenant importer scrapy
import scrapy
from scrapy.crawler import CrawlerProcess
from scrapy.utils.project import get_project_settings
import os
import time
from datetime import datetime

DEBUG:asyncio:Using selector: EpollSelector


# SCRAP Final

In [ ]:
class HelloWorkSpider(scrapy.Spider):
    name = 'hellowork'

    def __init__(self, max_pages, *args, **kwargs):
        super(HelloWorkSpider, self).__init__(*args, **kwargs)
        self.max_pages = max_pages
        self.scraped_pages = 0
        self.start_time = time.time()
        self.offres_count = 0

    def start_requests(self):
        pages_to_scrape = min(self.max_pages, 200)

        print(f"Démarrage du scraping de {pages_to_scrape} pages")
        print("=" * 50)

        for page in range(1, pages_to_scrape + 1):
            url = f"https://www.hellowork.com/fr-fr/emploi/recherche.html?p={page}"

            headers = {
                'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36',
                'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
            }

            yield scrapy.Request(
                url,
                callback=self.parse_liste,
                headers=headers,
                meta={'page': page},
                errback=self.errback_handler
            )

    def parse_liste(self, response):
        page = response.meta['page']
        self.scraped_pages += 1

        offres_trouvees = 0
        current_time = time.time()
        elapsed_time = current_time - self.start_time

        print(f"Page {page}/{self.max_pages} ", end="")

        # Cherche toutes les offres dans la liste
        offres = response.css('div[data-id-storage-target="item"]')

        if not offres:
            offres = response.css('ul[aria-label*="liste des offres"] li')

        if not offres:
            offres = response.css('li')

        for offre in offres:
            # Extraire l'ID de l'offre
            offre_id = offre.attrib.get('data-id-storage-item-id')

            if not offre_id:
                offre_id = offre.css('[data-id-storage-item-id]::attr(data-id-storage-item-id)').get()

            # Titre
            titre = offre.css('p.tw-typo-l::text').get()

            if not titre:
                titre = offre.css('h3 p.tw-typo-l::text').get()
                titre = offre.css('a[data-cy="offerTitle"] p.tw-typo-l::text').get()

            if titre or offre_id:
                # Entreprise
                entreprise = offre.css('p.tw-typo-s::text').get()
                if not entreprise:
                    entreprise = offre.css('a[data-cy="offerTitle"] p.tw-typo-s::text').get()

                # Localisation
                localisation = offre.css('div[data-cy="localisationCard"]::text').get()
                if not localisation:
                    localisation = offre.css('[data-cy*="localisation"]::text').get()

                # Contrat
                contrat = offre.css('div[data-cy="contractCard"]::text').get()
                if not contrat:
                    contrat = offre.css('[data-cy*="contractCard"]::text').get()

                # Date
                date = offre.css('div.tw-text-grey-500::text').get()
                if not date:
                    date = offre.css('div.tw-typo-s.tw-text-grey-500::text').get()

                # Salaire
                salaire = ''
                for div in offre.css('div.tw-typo-s-bold'):
                    text = ' '.join(div.css('::text').getall()).strip()
                    if text and ('€' in text or 'EUR' in text):
                        salaire = text
                        break

                if not salaire:
                    for span in offre.css('span.tw-typo-s-bold'):
                        text = ' '.join(span.css('::text').getall()).strip()
                        if text and ('€' in text or 'EUR' in text):
                            salaire = text
                            break

                # URL complète
                url_complete = ""
                if offre_id:
                    url_complete = f"https://www.hellowork.com/fr-fr/emplois/{offre_id}.html"
                else:
                    lien = offre.css('a[data-cy="offerTitle"]::attr(href)').get()
                    url_complete = f"https://www.hellowork.com{lien}" if lien else ""

                # Métadonnées
                meta_data = {
                    'page': page,
                    'offre_id': offre_id if offre_id else "",
                    'titre': titre.strip() if titre else "",
                    'entreprise': entreprise.strip() if entreprise else "",
                    'localisation': localisation.strip() if localisation else "",
                    'contrat': contrat.strip() if contrat else "",
                    'salaire': salaire.strip() if salaire else "",
                    'date': date.strip() if date else "",
                    'url_page': response.url,
                    'scraped_at': datetime.now().strftime('%Y-%m-%d %H:%M:%S'),
                }

                # Visiter la page détaillée si on a une URL
                if url_complete and offre_id:
                    self.offres_count += 1
                    offres_trouvees += 1

                    yield scrapy.Request(
                        url_complete,
                        callback=self.parse_detail,
                        headers={
                            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36',
                            'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
                        },
                        meta={'meta_data': meta_data, 'url_complete': url_complete},
                        errback=self.errback_handler_detail
                    )
                else:
                    # Données basiques si pas d'URL
                    item = {**meta_data,
                           'url': url_complete,
                           'mots_cles': '',
                           'domaine': '',
                           'nombre_tags': 0}
                    offres_trouvees += 1
                    yield item

        print(f"- {offres_trouvees} offres extraites")
        print(f"  Temps écoulé: {elapsed_time/60:.1f} minutes")

    def parse_detail(self, response):
        """Parse la page détaillée d'une offre"""
        meta_data = response.meta['meta_data']
        url_complete = response.meta['url_complete']

        tags = []
        domaine = ""

        # Chercher tous les tags
        tag_elements = response.css('ul.tw-flex.tw-flex-wrap.tw-gap-3 li')

        if not tag_elements:
            tag_elements = response.css('ul.tw-flex.tw-gap-3 li')

        if not tag_elements:
            tag_elements = response.css('li.tw-tag-secondary-s, li.tw-block.tw-tag-secondary-s, [class*="tag"]')

        for tag_element in tag_elements:
            # Exclure le tag de salaire
            if tag_element.css('button[data-cy="salary-tag-button"]'):
                continue

            # Extraire le texte
            tag_text = tag_element.css('::text').getall()
            tag_text = ' '.join([t.strip() for t in tag_text if t.strip()])

            if tag_text:
                # Ajouter le tag brut
                tags.append(tag_text)

                # Si le tag contient "•" et n'est pas un domaine déjà trouvé
                if '•' in tag_text and not domaine:
                    # Prendre la partie avant le "•" comme domaine
                    # Exemple: "Industrie Auto • Meca • Navale" -> "Industrie Auto"

                    domaine_temp = tag_text.split('•')[0].strip()
                    # Vérifier que ce n'est pas une localisation, contrat, etc.
                    if (not any(mot in domaine_temp.lower() for mot in ['cdi', 'cdd', 'stage', 'alternance', 'intérim']) and
                        not any(char.isdigit() for char in domaine_temp) and
                        '-' not in domaine_temp and  # Éviter les localisations
                        len(domaine_temp.split()) <= 4):
                        domaine = domaine_temp

        # Si pas de tag avec "•", chercher un tag qui pourrait être un domaine
        if not domaine and tags:
            for tag in tags:
                # Éviter les tags qui sont clairement autre chose
                tag_lower = tag.lower()
                if any(word in tag_lower for word in ['cdi', 'cdd', 'stage', 'alternance', 'intérim', 'temps', 'partiel', 'plein']):
                    continue
                if any(char.isdigit() for char in tag):  # Éviter les codes postaux
                    continue
                if '-' in tag and len(tag.split('-')) == 2 and tag.split('-')[1].strip().isdigit():  # Éviter "Ville - 75"
                    continue
                if 'ans' in tag_lower or 'expérience' in tag_lower or 'exp.' in tag_lower:  # Éviter expérience
                    continue
                if 'bac' in tag_lower or 'diplôme' in tag_lower or 'cap' in tag_lower or 'bep' in tag_lower:  # Éviter diplômes
                    continue
                if '€' in tag or 'euros' in tag_lower or 'salaire' in tag_lower:  # Éviter salaire
                    continue
                if 'télétravail' in tag_lower:  # Éviter télétravail
                    continue

                # Si le tag a entre 1 et 4 mots
                mots = tag.split()
                if 1 <= len(mots) <= 4:
                    domaine = tag
                    break

        # Garder tous les tags, même si doublons
        tags_text = ', '.join(tags) if tags else ''

        # Créer l'item
        item = {
            **meta_data,
            'url': url_complete,
            'mots_cles': tags_text,
            'domaine': domaine,
            'nombre_tags': len(tags),
        }

        print(f"  Offre {meta_data.get('offre_id', 'N/A')}: {len(tags)} tags, domaine: {domaine}")

        yield item

    def errback_handler(self, failure):
        page = failure.request.meta.get('page', 'inconnu')
        print(f"Erreur pour la page {page}")

    def errback_handler_detail(self, failure):
        url = failure.request.meta.get('url_complete', 'URL inconnue')
        print(f"Erreur pour la page détaillée {url}")

        meta_data = failure.request.meta.get('meta_data', {})
        if meta_data:
            item = {
                **meta_data,
                'url': failure.request.url,
                'mots_cles': '',
                'domaine': '',
                'nombre_tags': 0,
            }
            yield item

    def closed(self, reason):
        total_time = time.time() - self.start_time
        print("\n" + "=" * 50)
        print(f"Spider terminé: {reason}")
        print(f"Pages scrapées: {self.scraped_pages}")
        print(f"Offres visitées: {self.offres_count}")
        print(f"Temps total: {total_time/60:.1f} minutes")

# Fonction pour exécuter le spider
def run_spider(max_pages):
    settings = {
        'USER_AGENT': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36',
        'CONCURRENT_REQUESTS': 1,
        'DOWNLOAD_DELAY': 2,
        'ROBOTSTXT_OBEY': False,
        'RETRY_ENABLED': True,
        'RETRY_TIMES': 2,
        'LOG_LEVEL': 'INFO',
        'FEEDS': {
            'hellowork_offres_complete.csv': {
                'format': 'csv',
                'encoding': 'utf-8-sig',
                'overwrite': True,
            }
        }
    }

    process = CrawlerProcess(settings)
    process.crawl(HelloWorkSpider, max_pages=max_pages)
    process.start()

    # Analyse des résultats
    try:
        df = pd.read_csv('hellowork_offres_complete.csv', encoding='utf-8-sig')
        print("\n" + "=" * 50)
        print("ANALYSE DES RÉSULTATS")
        print("=" * 50)
        print(f"Total d'offres: {len(df):,}")
        print(f"Pages scrapées: {df['page'].nunique()}")

        print(f"\nNOUVELLES COLONNES:")
        print(f"- Offres avec ID: {df[df['offre_id'] != ''].shape[0]}")
        print(f"- Offres avec tags: {df[df['mots_cles'] != ''].shape[0]}")
        print(f"- Offres avec domaine: {df[df['domaine'] != ''].shape[0]}")

        if not df.empty:
            print(f"\nEXEMPLES:")
            for idx, row in df.head(3).iterrows():
                print(f"\nOffre {row['offre_id']}:")
                print(f"  Titre: {row['titre']}")
                print(f"  Entreprise: {row['entreprise']}")
                print(f"  Domaine: {row['domaine']}")
                print(f"  Tags: {row['mots_cles'][:100]}...")
                print(f"  Nombre tags: {row['nombre_tags']}")

        return df

    except FileNotFoundError:
        print("Aucune donnée récupérée.")
        return pd.DataFrame()
    except Exception as e:
        print(f"Erreur: {e}")
        return pd.DataFrame()

# Exécution
if __name__ == "__main__":
    df = run_spider(200)

    print("\n" + "=" * 50)
    print("TERMINÉ !")
    print("=" * 50)

INFO:scrapy.utils.log:Scrapy 2.13.4 started (bot: scrapybot)
2025-12-06 15:35:14 [scrapy.utils.log] INFO: Scrapy 2.13.4 started (bot: scrapybot)
INFO:scrapy.utils.log:Versions:
{'lxml': '6.0.2',
 'libxml2': '2.14.6',
 'cssselect': '1.3.0',
 'parsel': '1.10.0',
 'w3lib': '2.3.1',
 'Twisted': '25.5.0',
 'Python': '3.12.12 (main, Oct 10 2025, 08:52:57) [GCC 11.4.0]',
 'pyOpenSSL': '24.2.1 (OpenSSL 3.3.2 3 Sep 2024)',
 'cryptography': '43.0.3',
 'Platform': 'Linux-6.6.105+-x86_64-with-glibc2.35'}
2025-12-06 15:35:14 [scrapy.utils.log] INFO: Versions:
{'lxml': '6.0.2',
 'libxml2': '2.14.6',
 'cssselect': '1.3.0',
 'parsel': '1.10.0',
 'w3lib': '2.3.1',
 'Twisted': '25.5.0',
 'Python': '3.12.12 (main, Oct 10 2025, 08:52:57) [GCC 11.4.0]',
 'pyOpenSSL': '24.2.1 (OpenSSL 3.3.2 3 Sep 2024)',
 'cryptography': '43.0.3',
 'Platform': 'Linux-6.6.105+-x86_64-with-glibc2.35'}
INFO:scrapy.addons:Enabled addons:
[]
2025-12-06 15:35:14 [scrapy.addons] INFO: Enabled addons:
[]
DEBUG:scrapy.utils.log:Usin

Démarrage du scraping de 200 pages


DEBUG:scrapy.core.engine:Crawled (200) <GET https://www.hellowork.com/fr-fr/emploi/recherche.html?p=1> (referer: None)


Page 1/200 - 30 offres extraites
  Temps écoulé: 0.0 minutes


DEBUG:scrapy.core.engine:Crawled (200) <GET https://www.hellowork.com/fr-fr/emploi/recherche.html?p=2> (referer: None)


...

  Offre 71135657: 8 tags, domaine: Distribution


DEBUG:scrapy.core.engine:Crawled (200) <GET https://www.hellowork.com/fr-fr/emplois/71131527.html> (referer: https://www.hellowork.com/fr-fr/emploi/recherche.html?p=199)
DEBUG:scrapy.core.scraper:Scraped from <200 https://www.hellowork.com/fr-fr/emplois/71131527.html>
{'page': 199, 'offre_id': '71131527', 'titre': 'Manager de Rayons Frais ou Pgc H/F', 'entreprise': 'Auchan Retail France', 'localisation': 'Paris - 75', 'contrat': 'CDI', 'salaire': '32\u202f000 - 40\u202f000 € / an', 'date': 'il y a 2 jours', 'url_page': 'https://www.hellowork.com/fr-fr/emploi/recherche.html?p=199', 'scraped_at': '2025-12-06 19:20:00', 'url': 'https://www.hellowork.com/fr-fr/emplois/71131527.html', 'mots_cles': 'Paris - 75, CDI, Bac, Bac +2, Distribution • Commerce de gros, Exp. 2 ans min., Paris - 75, CDI', 'domaine': 'Distribution', 'nombre_tags': 8}


  Offre 71131527: 8 tags, domaine: Distribution


DEBUG:scrapy.core.engine:Crawled (200) <GET https://www.hellowork.com/fr-fr/emplois/71131870.html> (referer: https://www.hellowork.com/fr-fr/emploi/recherche.html?p=199)
DEBUG:scrapy.core.scraper:Scraped from <200 https://www.hellowork.com/fr-fr/emplois/71131870.html>
{'page': 199, 'offre_id': '71131870', 'titre': "Chef d'Equipe H/F", 'entreprise': 'Transgourmet', 'localisation': 'Saint-Martin-de-Crau - 13', 'contrat': 'CDI', 'salaire': '', 'date': 'il y a 2 jours', 'url_page': 'https://www.hellowork.com/fr-fr/emploi/recherche.html?p=199', 'scraped_at': '2025-12-06 19:20:00', 'url': 'https://www.hellowork.com/fr-fr/emplois/71131870.html', 'mots_cles': 'Saint-Martin-de-Crau - 13, CDI, Bac, Distribution • Commerce de gros, Industrie Agro-alimentaire, Exp. 2 à 5 ans, Saint-Martin-de-Crau - 13, CDI', 'domaine': 'Distribution', 'nombre_tags': 8}
INFO:scrapy.core.engine:Closing spider (finished)
2025-12-06 19:22:20 [scrapy.core.engine] INFO: Closing spider (finished)
INFO:scrapy.extensions.f

  Offre 71131870: 8 tags, domaine: Distribution

Spider terminé: finished
Pages scrapées: 200
Offres visitées: 6000
Temps total: 227.1 minutes

ANALYSE DES RÉSULTATS
Total d'offres: 5,409
Pages scrapées: 200

NOUVELLES COLONNES:
- Offres avec ID: 5409
- Offres avec tags: 5409
- Offres avec domaine: 5409

EXEMPLES:

Offre 73452413:
  Titre: Employé de Ménage-Repassage - à Domicile - - St Martin d'Hères et Alentours H/F
  Entreprise: O2
  Domaine: Services aux Personnes
  Tags: Saint-Martin-d'Hères - 38, CDI, Temps partiel, BEP, CAP, Bac, Services aux Personnes • Particuliers,...
  Nombre tags: 9

Offre 73438755:
  Titre: Technico-Commercial Itinérant H/F
  Entreprise: Roussely
  Domaine: Distribution
  Tags: Évreux - 27, CDI, Bac +2, Bac +3, Bac +4, Distribution • Commerce de gros, Exp. 1 an min., Évreux - ...
  Nombre tags: 8

Offre 73438741:
  Titre: Technico-Commercial Itinérant H/F
  Entreprise: Roussely
  Domaine: Distribution
  Tags: Chartres - 28, CDI, Bac +2, Bac +3, Bac +4, Dis